<h1 align=center><font size = 5>Starbucks in Quito, EC</font></h1>
<h1 align=center><font size = 4>Finding the Best Location for the First Starbucks in Quito </font></h1>
<h1 align=center><font size = 3>by Andrés Borja</font></h1>


## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Introduction</a>

2. <a href="#item2">Data</a>

    2.1 <a href="#item3">Data sources</a>
    
    2.2 <a href="#item4">Download and explore dataset</a>
    
    2.3 <a href="#item5">Data cleaning</a>
    
3. <a href="#item6">Data analysis</a>
    
    3.1 <a href="#item7">Exploring the neighborhoods in Quito</a>
    
    3.2 <a href="#item8">Analyzing each neighborhood’s venue categories</a>
    
    3.3 <a href="#item9">Clustering neighborhoods</a>
    
    3.4 <a href="#item10">Examining resulting clusters</a>

  
</font>
</div>

## 1. Introduction 
In spite pf being one of Latin America's fastest growing coffee producers, Ecuador does not have a Starbucks store yet, not even in its capital city, Quito. However, Quito is a big city; in order to guarantee its success, Starbucks should carefully and strategically plan where exactly to open its first store in Ecuador’s capital. They should try to pick the best area or neighborhood based on the kind of venues that already exist there, which should be economically tied to coffee shops. **By classifying the neighborhoods of Quito in terms of its extant venues, Starbucks could make a better informed decision of where to open their first store in Ecuador’s capital, thus improving the likelihood of their success.** Fortunately, several data science and machine learning techniques can help Starbucks explore and cluster Quito’s neighborhoods in order to better understand the city, its structure and its dynamics, so that they can accomplish their business goals. 

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt  

# import k-means and some asociated libraries for model evaluation for the clustering stage
from sklearn.cluster import KMeans, SpectralClustering
from sklearn.preprocessing import StandardScaler 

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


## 2. Data 

### 2.1 Data sources
In order to be able to classify Quito’s neighborhoods on a map, we will need a database which includes all of the **city’s neighborhoods with their geographical coordinates**. The city’s municipality website has several georeferenced databases of the city’s geopolitical and administrative divisions. We picked the databased named “Barrio - Sector”, from their [website](http://gobiernoabierto.quito.gob.ec/?page_id=1122). We downloaded the data, converted it to a JSON file using ArcGIS and stored it in our GitHub repository. 

The classification parameter will be the kinds of venues that exist in each neighborhood. This information will be obtained from Foursquare, a location data provider with information about all manner of venues and events within an area of interest. Such information includes venues names, categories, locations, menus, ratings and even pictures. We will be using using the [Foursquare API](https://developer.foursquare.com/docs/places-api/) to explore the **venues surrounding the coordinates for each neighborhood**, and then classifying the neighborhoods based on their assigned categories. 

### 2.2 Download and Explore Dataset

In [3]:
!wget -q -O 'uio_barrios_urbanos.json' https://raw.githubusercontent.com/andresborja42/Coursera_Capstone/master/uio_barrios_urbanos.json
print('Data downloaded!')

Data downloaded!


#### Load and explore the data

In [4]:
with open('uio_barrios_urbanos.json') as json_data:
    barrios_uio = json.load(json_data)

In [ ]:
barrios_uio

All the relevant data seems to be in the *features* key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [5]:
barrios_data = barrios_uio['features']

Let's take a look at the first item in this list.

In [7]:
barrios_data[0]

{'attributes': {'FID': 0,
  'NOMBRE': 'NUEVA VIDA',
  'BARRIO_ID': '01050014',
  'Lat_y': -0.273928072625,
  'Long_x': -78.5637147392},
 'geometry': {'rings': [[[492803.3856000006, 9969745.8419],
    [492867.42530000024, 9969782.9017],
    [493008.8746000007, 9969655.3123],
    [493001.6347000003, 9969645.5424],
    [492990.3047000002, 9969639.2724],
    [492982.8848000001, 9969635.9524],
    [492955.59490000084, 9969627.6625],
    [492919.9650999997, 9969613.6425],
    [492831.6054999996, 9969701.2221],
    [492803.3856000006, 9969745.8419]]]}}

#### Transform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

In [6]:
# Define the dataframe columns
column_names = ['ID', 'Neighborhood', 'Latitude', 'Longitude'] 

# Instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

We take a look at the dataframe to make sure that the columns are as intended.

In [9]:
neighborhoods

Empty DataFrame
Columns: [ID, Neighborhood, Latitude, Longitude]
Index: []

Now let's loop through the data and fill the dataframe one row at a time.

In [7]:
for data in barrios_data:
    ID = data['attributes']['BARRIO_ID'] 
    neighborhood_name = data['attributes']['NOMBRE']
    neighborhood_lat = data['attributes']['Lat_y']
    neighborhood_lon = data['attributes']['Long_x']
    
    neighborhoods = neighborhoods.append({'ID': ID,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [11]:
neighborhoods.head()

ID       Neighborhood  Latitude  Longitude
0  01050014         NUEVA VIDA -0.273928 -78.563715
1  01050026         VENCEREMOS -0.272159 -78.564992
2  04070005     AVIACION CIVIL -0.155464 -78.487854
3  01050017  S.MARTHA ALT CHIL -0.275713 -78.561793
4  02010005          LA RAYA A -0.255895 -78.543519

In [12]:
print(neighborhoods.shape)

(517, 4)


### 2.3 Data cleaning
The municipality’s neighborhoods database includes all of the neighborhoods that make up the Metropolitan District of Quito, which is classified in terms of urban and rural boroughs. There are a total of 1268 neighborhoods in the MD of Quito. We decided to work with the urban area neighborhoods only, because rural areas are too remote and isolated, with very low population density. Almost no venues could be found around the rural neighborhoods when exploring them through Foursquare, so it wouldn’t make sense to include them in our analysis. The urban area is made up of 516 neighborhoods. 

We now checked for missing values. By exploring the dataframe, we realized all those values in the "Neighborhood" column which start with the "SIN NOMBRE" string, which means "no name" in Spanish, are missing values. If we don't have manes for those neighborhoods, we better get rid of them. So we first replace the values which start with "SIN NOMBRE" for the Pandas object type for missing values, which is np.NaN

In [8]:
# Cleaning the dataframe 

neighborhoods.loc[neighborhoods['Neighborhood'].str.startswith("SIN NOMBRE"), 'Neighborhood'] = np.NaN
neighborhoods.head()

ID       Neighborhood  Latitude  Longitude
0  01050014         NUEVA VIDA -0.273928 -78.563715
1  01050026         VENCEREMOS -0.272159 -78.564992
2  04070005     AVIACION CIVIL -0.155464 -78.487854
3  01050017  S.MARTHA ALT CHIL -0.275713 -78.561793
4  02010005          LA RAYA A -0.255895 -78.543519

We verify if they are now of NaN type.

In [9]:
neighborhoods.isna().sum()

ID               0
Neighborhood    28
Latitude         0
Longitude        0
dtype: int64

And now we get rid of those 28 NaN values and reset the index.

In [10]:
neighborhoods = neighborhoods.dropna()
neighborhoods = neighborhoods.reset_index(drop=True)

In [16]:
neighborhoods.head()

ID       Neighborhood  Latitude  Longitude
0  01050014         NUEVA VIDA -0.273928 -78.563715
1  01050026         VENCEREMOS -0.272159 -78.564992
2  04070005     AVIACION CIVIL -0.155464 -78.487854
3  01050017  S.MARTHA ALT CHIL -0.275713 -78.561793
4  02010005          LA RAYA A -0.255895 -78.543519

In [17]:
print(neighborhoods.shape)

(489, 4)


So in the end, 28 of these urban neighborhoods did not have a name assigned in the database. We decided to exclude them from the analysis as well. In the end we kept **488 neighborhoods from Quito’s urban area**. 

#### Use geopy library to get the latitude and longitude values of Quito.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>uio_explorer</em>, as shown below.

In [11]:
address = 'Quito, EC'

geolocator = Nominatim(user_agent="uio_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geographical coordinates of Quito are {}, {}.'.format(latitude, longitude))

The geographical coordinates of Quito are -0.2201641, -78.5123274.


#### Create a map of Quito with neighborhoods superimposed on top.

In [12]:
# create map of Quito using latitude and longitude values
map_uio = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, ID, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['ID'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, ID)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_uio)  
    
map_uio

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [13]:
CLIENT_ID = 'IT10XUOI4FLKLXPX1HGNZ1SORXYGADP0UHVYLG5BQ0KHM3Z2' 
CLIENT_SECRET = 'FPXPR1NXOEZPETRUTNY43TQH3ZLDNPLVIFLDOPYDZ3HTDXFX' 
VERSION = '20200619' 

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: IT10XUOI4FLKLXPX1HGNZ1SORXYGADP0UHVYLG5BQ0KHM3Z2
CLIENT_SECRET:FPXPR1NXOEZPETRUTNY43TQH3ZLDNPLVIFLDOPYDZ3HTDXFX


#### Let's explore the first neighborhood in our dataframe.

In [14]:
neighborhoods.loc[0, 'Neighborhood']

'NUEVA VIDA'

Get the neighborhood's latitude and longitude values.

In [15]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of NUEVA VIDA are -0.273928072625, -78.5637147392.


#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [16]:
LIMIT = 50
radius = 1000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=IT10XUOI4FLKLXPX1HGNZ1SORXYGADP0UHVYLG5BQ0KHM3Z2&client_secret=FPXPR1NXOEZPETRUTNY43TQH3ZLDNPLVIFLDOPYDZ3HTDXFX&v=20200619&ll=-0.273928072625,-78.5637147392&radius=1000&limit=50'

Send the GET request and examine the resutls.

In [17]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ef529cf513bb60f51e6392f'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Chillogallo',
  'headerFullLocation': 'Chillogallo, Quito',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 3,
  'suggestedBounds': {'ne': {'lat': -0.264928063624991,
    'lng': -78.55473143157906},
   'sw': {'lat': -0.28292808162500904, 'lng': -78.57269804682093}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5340231c498e0578b618c49d',
       'name': 'Encebollado Manabita',
       'location': {'lat': -0.27782320976257324,
        'lng': -78.55779266357422,
        'labeledLatLngs': [{'label': 'display',
          'l

In [19]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [20]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name                 categories       lat        lng
0  Encebollado Manabita  Latin American Restaurant -0.277823 -78.557793
1    Fritadas El Juncal                  BBQ Joint -0.272065 -78.556384
2            El Español             Breakfast Spot -0.274300 -78.555000

In [21]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

3 venues were returned by Foursquare.


We now have access to both the neighborhoods and the venues datasets. We can now start exploring the neighborhoods based on their surrounding venues.

## 3. Data analysis

### 3.1 Exploring the Neighborhoods in Quito

#### We create a function to repeat the same process to all the neighborhoods in Quito

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now we run the above function on each neighborhood and create a new dataframe called *uio_venues*.

In [23]:
uio_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

NUEVA VIDA
VENCEREMOS
AVIACION CIVIL
S.MARTHA ALT CHIL
LA RAYA A
RUPERTO ALARCON
SAN ANTONIO
LA LIBERTAD BAJO
STA BARBARA ALTA
SOLANDA
CELAUR
EUGENIO ESPEJO
SANTIAGO 1
S.ROSA CHIL 3ETP
S.TOSPAMBA
UNIVERSI CENTRAL
LOS PEDESTALES
QUITO W
20 DE MAYO
PRESIDENCIA REPUBLICA
S. TOSPAMBA
FRANKLIN TELLO
S.FERNANDO
VISTA HERMOSA
COLINAS DEL SUR
FELIXRIVADENEIRA
DAMMER 2
STA. BARBARA BAJA
TACHINA 2
LA MERCED
ANA MARIA
ALEGRIA N 1
STA.ROSA SINGUNA
LOS CIPRESES
SANTA INES 2
CAUSAYLLACTA
EL GUABO
S.ROSA ALTA CHIL
HDA GUAPULO
STA BARBARA BAJA
LOS CIPRESES
MIRAFLORES ALTO
S.CARLOS VENCEN
EL TRANSITO
CAMILO PONCE
PROF MUNICIPALES
LA ISLA
AREA VERDE
LA FLORIDA
MALDONADO
MADRIGAL
FERROVIARIA ALTA
VIRGENPATA
S.PEDRO MONJAS
S.AGUSTIN
EL PARAISO
BELLA MARIA
LOTIZ QUINGAIZA
ESPERANZA BAR
JARDINES DEL BATAN
FERROVIARIA MEDIA
MIRAFLORES BAJO
COND.S.PICHINCHA
EL ROCIO
LA ESTANCIA
STA.LUCIA ALTA
GERMAN AVILA
ARGENTINA
JOSEFINAENRIQUEZ
EL CARMEN
PALUCO B
LIBERTAD BAJO
LOS ARRAYANES
DAMMER
EL EDEN
EL PEDREGAL
MIRA

#### Let's check the size of the resulting dataframe

In [24]:
print(uio_venues.shape)
uio_venues.head(10)

(2547, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0      NUEVA VIDA              -0.273928              -78.563715   
1      NUEVA VIDA              -0.273928              -78.563715   
2      VENCEREMOS              -0.272159              -78.564992   
3      VENCEREMOS              -0.272159              -78.564992   
4  AVIACION CIVIL              -0.155464              -78.487854   
5  AVIACION CIVIL              -0.155464              -78.487854   
6  AVIACION CIVIL              -0.155464              -78.487854   
7  AVIACION CIVIL              -0.155464              -78.487854   
8  AVIACION CIVIL              -0.155464              -78.487854   
9  AVIACION CIVIL              -0.155464              -78.487854   

                                             Venue  Venue Latitude  \
0                                     S29C Y OE12E       -0.272326   
1                         Mariachi Fiesta Mexicana       -0.275757   
2                                     S29C Y OE12E       -0.272326   
3                         Mariachi Fiesta Mexicana       -0.275757   
4                              Menestras del Primo       -0.155252   
5                                        Cachorros       -0.153951   
6                                    La Michoacana       -0.158246   
7                        El Manglar De Las Conchas       -0.155171   
8  Los legitimos helados de paila de la Concepcion       -0.153525   
9                                      La tortilla       -0.153528   

   Venue Longitude      Venue Category  
0       -78.563025            Bus Stop  
1       -78.565411   Convention Center  
2       -78.563025            Bus Stop  
3       -78.565411   Convention Center  
4       -78.488654          Restaurant  
5       -78.491237                 Gym  
6       -78.490567  Mexican Restaurant  
7       -78.488566  Seafood Restaurant  
8       -78.491681      Ice Cream Shop  
9       -78.490682    Arepa Restaurant

We now check how many venues were returned for each neighborhood.

In [25]:
uio_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                
10 DE JUNIO                                     4                       4   
1RA ZONA AEREA                                  4                       4   
1RO MAYO MONJAS                                 5                       5   
2 DE FEBRERO                                    5                       5   
23 DE MAYO                                      1                       1   
23 JUNIO BARRIO                                 4                       4   
6 DE DICIEMBRE                                 26                      26   
AEREONAUTICO                                    8                       8   
AEROPUERTO                                     14                      14   
AGUA CLARA                                      5                       5   
ALLPALLACTA                                     4                       4   
ALMA LOJANA                                     4                       4   
ALVARO PEREZ INDEPENDIENTE                      3                       3   
AMERICA                                         6                       6   
ANA LUISA                                      12                      12   
ANA MARIA BAJO                                  1                       1   
ANDALUCIA                                      11                      11   
AREA DE PROTECCION                              5                       5   
AREA PROTECCION                                 2                       2   
AREA VERDE                                      5                       5   
ARGELIA ALTA                                    2                       2   
ARGELIA INTERMEDIA                              2                       2   
ATAHUALPA E                                     4                       4   
ATAHUALPA W                                     4                       4   
ATUCUCHO                                        3                       3   
AVIACION CIVIL                                 14                      14   
AYMESA                                          1                       1   
BAKER                                           7                       7   
BALCON DEL NORTE                                4                       4   
BARRIONUEVO                                     9                       9   
BATAN ALTO                                     14                      14   
BATAN BAJO                                     94                      94   
BEATERIO ANDINAT                                1                       1   
BELLA AURORA                                    2                       2   
BELLA MARIA                                     2                       2   
BELLAVI CARRETAS                                2                       2   
BELLAVISTA                                     22                      22   
BELLAVISTA ALTA                                 1                       1   
BELLAVISTA ALTO                                 6                       6   
BELLAVISTA SUR                                  2                       2   
BENALCAZAR CD                                  50                      50   
BETANIA                                         5                       5   
BILOXI                                          5                       5   
BOLIVA RODRIGUEZ                                2                       2   
BUENOS AIRES                                    2                       2   
C.T CONTRALORIA                                 4                       4   
CALIFORN BONANZA                                5                       5   
CALZADO 1 MAYO                                  4                       4   
CAMINO EUCALIPTO                                1                       1   
CAMPO ALEGRE                                    2                       2   
CARCELEN BAJO           

#### Let's find out how many unique categories can be curated from all the returned venues

In [26]:
print('There are {} uniques categories.'.format(len(uio_venues['Venue Category'].unique())))

There are 217 uniques categories.


### 3.2 Analyzing each neighborhood's venue categories

**One hot encoding** is a process by which categorical variables are converted into a form that could be provided to ML algorithms to do a better job in prediction. For the K-means clustering algorithm, all unique items under "Venue Category" are one-hot encoded.

In [27]:
# one hot encoding
uio_onehot = pd.get_dummies(uio_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
uio_onehot['Neighborhood'] = uio_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [uio_onehot.columns[-1]] + list(uio_onehot.columns[:-1])
uio_onehot = uio_onehot[fixed_columns]

uio_onehot.head()

Neighborhood  Airport Terminal  American Restaurant  Arepa Restaurant  \
0      NUEVA VIDA                 0                    0                 0   
1      NUEVA VIDA                 0                    0                 0   
2      VENCEREMOS                 0                    0                 0   
3      VENCEREMOS                 0                    0                 0   
4  AVIACION CIVIL                 0                    0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                     0                 0                   0            0   
1                     0                 0                   0            0   
2                     0                 0                   0            0   
3                     0                 0                   0            0   
4                     0                 0                   0            0   

   Auto Workshop  BBQ Joint  Bagel Shop  Bakery  Bar  Bed & Breakfast  \
0              0          0           0       0    0                0   
1              0          0           0       0    0                0   
2              0          0           0       0    0                0   
3              0          0           0       0    0                0   
4              0          0           0       0    0                0   

   Beer Bar  Beer Garden  Big Box Store  Bike Shop  Bookstore  Boutique  \
0         0            0              0          0          0         0   
1         0            0              0          0          0         0   
2         0            0              0          0          0         0   
3         0            0              0          0          0         0   
4         0            0              0          0          0         0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  Buffet  \
0              0                     0               0        0       0   
1              0                     0               0        0       0   
2              0                     0               0        0       0   
3              0                     0               0        0       0   
4              0                     0               0        0       0   

   Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0             0              0         0            0         1   
1             0              0         0            0         0   
2             0              0         0            0         1   
3             0              0         0            0         0   
4             0              0         0            0         0   

   Business Service  Butcher  Cafeteria  Café  Cajun / Creole Restaurant  \
0                 0        0          0     0                          0   
1                 0        0          0     0                          0   
2                 0        0          0     0                          0   
3                 0        0          0     0                          0   
4                 0        0          0     0                          0   

   Camera Store  Campground  Cantonese Restaurant  Cheese Shop  \
0             0           0                     0            0   
1             0           0                     0            0   
2             0           0                     0            0   
3             0           0                     0            0   
4             0           0                     0            0   

   Chinese Restaur

And let's examine the new dataframe size.

In [28]:
uio_onehot.shape

(2547, 218)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [29]:
uio_grouped = uio_onehot.groupby('Neighborhood').mean().reset_index()
uio_grouped

Neighborhood  Airport Terminal  American Restaurant  \
0                   10 DE JUNIO          0.000000             0.000000   
1                1RA ZONA AEREA          0.000000             0.000000   
2               1RO MAYO MONJAS          0.000000             0.000000   
3                  2 DE FEBRERO          0.000000             0.000000   
4                    23 DE MAYO          0.000000             0.000000   
5               23 JUNIO BARRIO          0.000000             0.000000   
6                6 DE DICIEMBRE          0.000000             0.000000   
7                  AEREONAUTICO          0.000000             0.000000   
8                    AEROPUERTO          0.071429             0.000000   
9                    AGUA CLARA          0.000000             0.000000   
10                  ALLPALLACTA          0.000000             0.000000   
11                  ALMA LOJANA          0.000000             0.000000   
12   ALVARO PEREZ INDEPENDIENTE          0.000000             0.000000   
13                      AMERICA          0.000000             0.000000   
14                    ANA LUISA          0.000000             0.000000   
15               ANA MARIA BAJO          0.000000             0.000000   
16                    ANDALUCIA          0.000000             0.000000   
17           AREA DE PROTECCION          0.000000             0.000000   
18              AREA PROTECCION          0.000000             0.000000   
19                   AREA VERDE          0.000000             0.000000   
20                 ARGELIA ALTA          0.000000             0.000000   
21           ARGELIA INTERMEDIA          0.000000             0.000000   
22                  ATAHUALPA E          0.000000             0.000000   
23                  ATAHUALPA W          0.000000             0.000000   
24                     ATUCUCHO          0.000000             0.000000   
25               AVIACION CIVIL          0.000000             0.000000   
26                       AYMESA          0.000000             0.000000   
27                        BAKER          0.000000             0.000000   
28             BALCON DEL NORTE          0.000000             0.000000   
29                  BARRIONUEVO          0.000000             0.000000   
30                   BATAN ALTO          0.000000             0.000000   
31                   BATAN BAJO          0.000000             0.010638   
32             BEATERIO ANDINAT          0.000000             0.000000   
33                 BELLA AURORA          0.000000             0.000000   
34                  BELLA MARIA          0.000000             0.000000   
35             BELLAVI CARRETAS          0.000000             0.000000   
36                   BELLAVISTA          0.000000             0.000000   
37              BELLAVISTA ALTA          0.000000             0.000000   
38              BELLAVISTA ALTO          0.000000             0.000000   
39               BELLAVISTA SUR          0.000000             0.000000   
40                BENALCAZAR CD          0.000000             0.000000   
41                      BETANIA          0.000000             0.000000   
42                       BILOXI          0.000000             0.000000   
43             BOLIVA RODRIGUEZ          0.000000             0.000000   
44                 BUENOS AIRES          0.000000             0.000000   
45              C.T CONTRALORIA          0.000000             0.000000   
46             CALIFORN BONANZA          0.000000             0.000000   
47               CALZADO 1 MAYO          0.000000             0.000000   
48             CAMINO EUCALIPTO          0.000000             0.000000   
49                 CAMPO ALEGRE          0.000000             0.000000   
50                CARCELEN BAJO          0.000000             0.000000   
51                 CARCELEN BEV          0.000000             0.000000   
52            CARCELEN FV PONCE          0.000000             0.000000   
53               CARCEL

#### Let's confirm the new size

In [30]:
uio_grouped.shape

(355, 218)

#### We now print each neighborhood along with the top 5 most common venues in it

In [31]:
num_top_venues = 5

for hood in uio_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = uio_grouped[uio_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----10 DE JUNIO----
                  venue  freq
0  Gym / Fitness Center  0.25
1            Restaurant  0.25
2    Athletics & Sports  0.25
3         Shopping Mall  0.25
4      Airport Terminal  0.00


----1RA ZONA AEREA----
                venue  freq
0         Bus Station  0.25
1         Coffee Shop  0.25
2  Seafood Restaurant  0.25
3         Pizza Place  0.25
4    Airport Terminal  0.00


----1RO MAYO MONJAS----
                        venue  freq
0  Construction & Landscaping   0.2
1                        Park   0.2
2               Auto Workshop   0.2
3                   BBQ Joint   0.2
4          Seafood Restaurant   0.2


----2 DE FEBRERO----
                venue  freq
0          Restaurant   0.2
1            Pharmacy   0.2
2    Business Service   0.2
3    Asian Restaurant   0.2
4  Seafood Restaurant   0.2


----23 DE MAYO----
                  venue  freq
0                 Hotel   1.0
1      Airport Terminal   0.0
2             Pet Store   0.0
3          Noodle House   0.0
4  

#### We save that into a *pandas* dataframe

First, we write a function to sort the venues in descending order.

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = uio_grouped['Neighborhood']

for ind in np.arange(uio_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(uio_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood          1st Most Common Venue  \
0                   10 DE JUNIO                     Restaurant   
1                1RA ZONA AEREA                    Bus Station   
2               1RO MAYO MONJAS                           Park   
3                  2 DE FEBRERO               Business Service   
4                    23 DE MAYO                          Hotel   
5               23 JUNIO BARRIO                         Bakery   
6                6 DE DICIEMBRE             Seafood Restaurant   
7                  AEREONAUTICO                   Soccer Field   
8                    AEROPUERTO                    Pizza Place   
9                    AGUA CLARA           Fast Food Restaurant   
10                  ALLPALLACTA                     Public Art   
11                  ALMA LOJANA           Fast Food Restaurant   
12   ALVARO PEREZ INDEPENDIENTE              Convenience Store   
13                      AMERICA                         Bakery   
14                    ANA LUISA                         Bakery   
15               ANA MARIA BAJO              Convenience Store   
16                    ANDALUCIA                       Pharmacy   
17           AREA DE PROTECCION                    Bus Station   
18              AREA PROTECCION                   Dessert Shop   
19                   AREA VERDE            Sporting Goods Shop   
20                 ARGELIA ALTA                          Hotel   
21           ARGELIA INTERMEDIA                   Burger Joint   
22                  ATAHUALPA E                           Park   
23                  ATAHUALPA W                      Juice Bar   
24                     ATUCUCHO                    Music Venue   
25               AVIACION CIVIL                     Restaurant   
26                       AYMESA                   Funeral Home   
27                        BAKER                            Bar   
28             BALCON DEL NORTE                    Pizza Place   
29                  BARRIONUEVO                    Pizza Place   
30                   BATAN ALTO                 Sandwich Place   
31                   BATAN BAJO                   Burger Joint   
32             BEATERIO ANDINAT                  Grocery Store   
33                 BELLA AURORA     Construction & Landscaping   
34                  BELLA MARIA                     Restaurant   
35             BELLAVI CARRETAS                    Bus Station   
36                   BELLAVISTA                      Gastropub   
37              BELLAVISTA ALTA                     Food Truck   
38              BELLAVISTA ALTO                     Art Museum   
39               BELLAVISTA SUR                   Dessert Shop   
40                BENALCAZAR CD             Italian Restaurant   
41                      BETANIA                      BBQ Joint   
42                       BILOXI                     Restaurant   
43             BOLIVA RODRIGUEZ           Fast Food Restaurant   
44                 BUENOS AIRES                            Gym   
45              C.T CONTRALORIA                    Pizza Place   
46             CALIFORN BONANZA                 Ice Cream Shop   
47               CALZADO 1 MAYO             Chinese Restaurant   
48             CAMINO EUCALIPTO                  Movie Theater   
49                 CAMPO ALEGRE           Arts & Entertainment   
50                CARCELEN BAJO                       Boutique   
51                 CARCELEN BEV                    Pizza Place   
52            CARCELEN FV PONCE           Fast Food Restaurant   
53               CARCELEN LIBRE                           Park   
54                     CARRETAS                 Cosmetics Shop   
55                   CAUPICHO I                  Grocery Store   
56                 CAUPICHO III                            Bar   
57                 CAUSAYLLACTA                    Bus Station   
58           CDLA UNIVERSITARIA                   Burger Joint   
59                 CDLA. GATAZO              Martial Arts D

### 3.3 Clustering Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [34]:
# set number of clusters
kclusters = 5

uio_grouped_clustering = uio_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(init="k-means++", n_clusters=kclusters, n_init=25, random_state=0).fit(uio_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([4, 3, 3, 3, 4, 4, 3, 4, 4, 3], dtype=int32)

We now proceed to create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [35]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

uio_merged = neighborhoods

# merge 'uio_merged' with 'neighborhoods' to add latitude/longitude for each neighborhood
uio_merged = uio_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

In [36]:
uio_merged.head(10)

ID       Neighborhood  Latitude  Longitude  Cluster Labels  \
0  01050014         NUEVA VIDA -0.273928 -78.563715             4.0   
1  01050026         VENCEREMOS -0.272159 -78.564992             4.0   
2  04070005     AVIACION CIVIL -0.155464 -78.487854             4.0   
3  01050017  S.MARTHA ALT CHIL -0.275713 -78.561793             4.0   
4  02010005          LA RAYA A -0.255895 -78.543519             4.0   
5  04060013    RUPERTO ALARCON -0.123700 -78.514805             4.0   
6  01050029        SAN ANTONIO -0.288270 -78.578933             NaN   
7  03020006   LA LIBERTAD BAJO -0.224198 -78.524245             NaN   
8  02010015   STA BARBARA ALTA -0.262981 -78.560950             NaN   
9  02020010            SOLANDA -0.268909 -78.539185             4.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0     Convention Center              Bus Stop                   Zoo   
1     Convention Center              Bus Stop                   Zoo   
2            Restaurant           Pizza Place              Pharmacy   
3              Bus Stop                   Zoo   Empanada Restaurant   
4            Restaurant             Cafeteria           Pizza Place   
5     Electronics Store                   Zoo                  Food   
6                   NaN                   NaN                   NaN   
7                   NaN                   NaN                   NaN   
8                   NaN                   NaN                   NaN   
9     Convenience Store                 Plaza          Dessert Shop   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Electronics Store           Flower Shop           Flea Market   
1          Electronics Store           Flower Shop           Flea Market   
2         Seafood Restaurant      Sculpture Garden    Chinese Restaurant   
3                       Food           Flower Shop           Flea Market   
4  Latin American Restaurant                Garden             BBQ Joint   
5                Flower Shop           Flea Market                 Field   
6                        NaN                   NaN                   NaN   
7                        NaN                   NaN                   NaN   
8                        NaN                   NaN                   NaN   
9              Big Box Store                  Park                   Zoo   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                 Field  Fast Food Restaurant        Farmers Market   
1                 Field  Fast Food Restaurant        Farmers Market   
2    Mexican Restaurant                   Gym  Pakistani Restaurant   
3                 Field  Fast Food Restaurant        Farmers Market   
4                   Zoo   Empanada Restaurant           Flea Market   
5  Fast Food Restaurant        Farmers Market               Factory   
6                   NaN                   NaN                   NaN   
7                   NaN                   NaN                   NaN   
8                   NaN                   NaN                   NaN   
9   Empanada Restaurant           Flower Shop           Flea Market   

  10th Most Common Venue  
0                Factory  
1                Factory  
2    Fried Chicken Joint  
3                Factory  
4                  Field  
5            Event Space  
6                    NaN  
7                    NaN  
8                    NaN  
9                  Field

There is a certain number of neighborhoods which don't have any venue nearby the established 500 radius. These are probably marginal neighborhoods, located far away from populated areas. We will not be able to include those neighborhoods because they will likely be clustered together by the algorithm and such a cluster (made of neighborhoods without any nearby venues) does not serve the purpose of our analysis. So we will drop the neighborhoods which contain NaN values for venues.

In [37]:
uio_merged.dropna('index', inplace=True)
uio_merged.reset_index(inplace=True)
uio_merged.head(10)

index        ID       Neighborhood  Latitude  Longitude  Cluster Labels  \
0      0  01050014         NUEVA VIDA -0.273928 -78.563715             4.0   
1      1  01050026         VENCEREMOS -0.272159 -78.564992             4.0   
2      2  04070005     AVIACION CIVIL -0.155464 -78.487854             4.0   
3      3  01050017  S.MARTHA ALT CHIL -0.275713 -78.561793             4.0   
4      4  02010005          LA RAYA A -0.255895 -78.543519             4.0   
5      5  04060013    RUPERTO ALARCON -0.123700 -78.514805             4.0   
6      9  02020010            SOLANDA -0.268909 -78.539185             4.0   
7     11  01050009     EUGENIO ESPEJO -0.273179 -78.558200             4.0   
8     12  02060012         SANTIAGO 1 -0.250375 -78.539400             4.0   
9     13  01050021   S.ROSA CHIL 3ETP -0.272262 -78.562653             4.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0     Convention Center              Bus Stop                   Zoo   
1     Convention Center              Bus Stop                   Zoo   
2            Restaurant           Pizza Place              Pharmacy   
3              Bus Stop                   Zoo   Empanada Restaurant   
4            Restaurant             Cafeteria           Pizza Place   
5     Electronics Store                   Zoo                  Food   
6     Convenience Store                 Plaza          Dessert Shop   
7        Breakfast Spot            Restaurant             BBQ Joint   
8           Supermarket           Pizza Place              Pharmacy   
9     Convention Center     Electronics Store                  Food   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Electronics Store           Flower Shop           Flea Market   
1          Electronics Store           Flower Shop           Flea Market   
2         Seafood Restaurant      Sculpture Garden    Chinese Restaurant   
3                       Food           Flower Shop           Flea Market   
4  Latin American Restaurant                Garden             BBQ Joint   
5                Flower Shop           Flea Market                 Field   
6              Big Box Store                  Park                   Zoo   
7                        Zoo   Empanada Restaurant                  Food   
8              Shopping Mall                   Zoo            Donut Shop   
9                Flower Shop           Flea Market                 Field   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                 Field  Fast Food Restaurant        Farmers Market   
1                 Field  Fast Food Restaurant        Farmers Market   
2    Mexican Restaurant                   Gym  Pakistani Restaurant   
3                 Field  Fast Food Restaurant        Farmers Market   
4                   Zoo   Empanada Restaurant           Flea Market   
5  Fast Food Restaurant        Farmers Market               Factory   
6   Empanada Restaurant           Flower Shop           Flea Market   
7           Flower Shop           Flea Market                 Field   
8                 Field  Fast Food Restaurant        Farmers Market   
9  Fast Food Restaurant        Farmers Market               Factory   

  10th Most Common Venue  
0                Factory  
1                Factory  
2    Fried Chicken Joint  
3                Factory  
4                  Field  
5            Event Space  
6                  Field  
7   Fast Food Restaurant  
8                Factory  
9            Event Space

And finally, we convert the data type of the 'Cluster labels' column, which ended up as a float but should in fact be an integer for the map we will create later.

In [38]:
uio_merged['Cluster Labels'] = uio_merged['Cluster Labels'].astype(int)

In [39]:
uio_merged.head(10)

index        ID       Neighborhood  Latitude  Longitude  Cluster Labels  \
0      0  01050014         NUEVA VIDA -0.273928 -78.563715               4   
1      1  01050026         VENCEREMOS -0.272159 -78.564992               4   
2      2  04070005     AVIACION CIVIL -0.155464 -78.487854               4   
3      3  01050017  S.MARTHA ALT CHIL -0.275713 -78.561793               4   
4      4  02010005          LA RAYA A -0.255895 -78.543519               4   
5      5  04060013    RUPERTO ALARCON -0.123700 -78.514805               4   
6      9  02020010            SOLANDA -0.268909 -78.539185               4   
7     11  01050009     EUGENIO ESPEJO -0.273179 -78.558200               4   
8     12  02060012         SANTIAGO 1 -0.250375 -78.539400               4   
9     13  01050021   S.ROSA CHIL 3ETP -0.272262 -78.562653               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0     Convention Center              Bus Stop                   Zoo   
1     Convention Center              Bus Stop                   Zoo   
2            Restaurant           Pizza Place              Pharmacy   
3              Bus Stop                   Zoo   Empanada Restaurant   
4            Restaurant             Cafeteria           Pizza Place   
5     Electronics Store                   Zoo                  Food   
6     Convenience Store                 Plaza          Dessert Shop   
7        Breakfast Spot            Restaurant             BBQ Joint   
8           Supermarket           Pizza Place              Pharmacy   
9     Convention Center     Electronics Store                  Food   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Electronics Store           Flower Shop           Flea Market   
1          Electronics Store           Flower Shop           Flea Market   
2         Seafood Restaurant      Sculpture Garden    Chinese Restaurant   
3                       Food           Flower Shop           Flea Market   
4  Latin American Restaurant                Garden             BBQ Joint   
5                Flower Shop           Flea Market                 Field   
6              Big Box Store                  Park                   Zoo   
7                        Zoo   Empanada Restaurant                  Food   
8              Shopping Mall                   Zoo            Donut Shop   
9                Flower Shop           Flea Market                 Field   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                 Field  Fast Food Restaurant        Farmers Market   
1                 Field  Fast Food Restaurant        Farmers Market   
2    Mexican Restaurant                   Gym  Pakistani Restaurant   
3                 Field  Fast Food Restaurant        Farmers Market   
4                   Zoo   Empanada Restaurant           Flea Market   
5  Fast Food Restaurant        Farmers Market               Factory   
6   Empanada Restaurant           Flower Shop           Flea Market   
7           Flower Shop           Flea Market                 Field   
8                 Field  Fast Food Restaurant        Farmers Market   
9  Fast Food Restaurant        Farmers Market               Factory   

  10th Most Common Venue  
0                Factory  
1                Factory  
2    Fried Chicken Joint  
3                Factory  
4                  Field  
5            Event Space  
6                  Field  
7   Fast Food Restaurant  
8                Factory  
9            Event Space

Finally, let's visualize the resulting clusters

In [41]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(uio_merged['Latitude'], uio_merged['Longitude'], uio_merged['Neighborhood'], uio_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### 3.4 Examining Resulting Clusters

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, we could then assign a name to each cluster.

#### Cluster 1

In [41]:
uio_merged.loc[uio_merged['Cluster Labels'] == 0, uio_merged.columns[[2] + list(range(5, uio_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
17    STA. BARBARA BAJA               0                  Park   
27      MIRAFLORES ALTO               0                  Park   
109        SAN SALVADOR               0        Scenic Lookout   
158            TOCTIUCO               0      Business Service   
199  ARGELIA INTERMEDIA               0          Burger Joint   
236      PAVON GRIJALVA               0                  Park   
276  CONSEJO PROVINCIAL               0                  Park   
298        CAMPO ALEGRE               0  Arts & Entertainment   
303       LAS BROMELIAS               0  Arts & Entertainment   
325        CAMPO ALEGRE               0  Arts & Entertainment   
363    SUCRE FUNDEPORTE               0                  Park   
370     PROTEC. LA MENA               0                  Park   
373  PROTEC. COCHAPAMBA               0                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
17      Convenience Store             Nightclub                 Plaza   
27                    Zoo   Empanada Restaurant                  Food   
109                  Park                   Zoo            Donut Shop   
158                  Park                   Zoo   Empanada Restaurant   
199                  Park   Empanada Restaurant                  Food   
236                   Zoo   Empanada Restaurant                  Food   
276                   Zoo   Empanada Restaurant                  Food   
298                  Park                   Zoo   Empanada Restaurant   
303                  Park                   Zoo   Empanada Restaurant   
325                  Park                   Zoo   Empanada Restaurant   
363                   Zoo   Empanada Restaurant                  Food   
370                   Zoo   Empanada Restaurant                  Food   
373                   Zoo   Empanada Restaurant                  Food   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
17                    Zoo           Flea Market                 Field   
27            Flower Shop           Flea Market                 Field   
109           Flea Market                 Field  Fast Food Restaurant   
158           Flower Shop           Flea Market                 Field   
199           Flower Shop           Flea Market                 Field   
236           Flower Shop           Flea Market                 Field   
276           Flower Shop           Flea Market                 Field   
298                  Food           Flower Shop           Flea Market   
303                  Food           Flower Shop           Flea Market   
325                  Food           Flower Shop           Flea Market   
363           Flower Shop           Flea Market                 Field   
370           Flower Shop           Flea Market                 Field   
373           Flower Shop           Flea Market                 Field   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
17   Fast Food Restaurant        Farmers Market                Factory  
27   Fast Food Restaurant        Farmers Market                Factory  
109        Farmers Market               Factory            Event Space  
158  Fast Food Restaurant        Farmers Market                Factory  
199  Fast Food Restaurant        Farmers Market                Factory  
236  Fast Food Restaurant        Farmers Market                Factory  
276  Fast Food Restaurant        Farmers Market                Factory  
298                 Field  Fast Food Restaurant         Farmers Market  
303                 Field  Fast Food Restaurant         Farmers Market  
325                 Field  Fast Food Restaurant         Farmers Market  
363  Fast Food Restaurant        Farmers Market                Factory  
370  Fast Food Restaurant        Farmers Market                Factory  
373  Fast Food Restaurant        Farmers Market                Factory

This cluster's most common venues seem to be mainly parks, zoos and fields, so it would not be a good match for Starbucks.

#### Cluster 2

In [42]:
uio_merged.loc[uio_merged['Cluster Labels'] == 1, uio_merged.columns[[2] + list(range(5, uio_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
22                 CAUSAYLLACTA               1           Bus Station   
43                     EL ROCIO               1           Bus Station   
68                      LA TOLA               1               Brewery   
71           AREA DE PROTECCION               1           Bus Station   
106  ALVARO PEREZ INDEPENDIENTE               1     Convenience Store   
133                   LULUNCOTO               1           Bus Station   
157                HUAYRALLACTA               1           Bus Station   
165                 EL COMERCIO               1           Bus Station   
166            LOS LIBERTADORES               1     Martial Arts Dojo   
211                     LA LOMA               1           Bus Station   
252                LA TOLA BAJA               1           Bus Station   
259                 ALLPALLACTA               1            Public Art   
279            BELLAVI CARRETAS               1           Bus Station   

         2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
22                         Zoo     Empanada Restaurant                  Food   
43        Fast Food Restaurant          Farmers Market        Soccer Stadium   
68                        Park             Bus Station                Hostel   
71                  Art Museum                     Zoo   Empanada Restaurant   
106                Bus Station        Department Store                   Zoo   
133             Breakfast Spot              Art Museum                   Zoo   
157                        Zoo     Empanada Restaurant                  Food   
165                   Pharmacy             Auto Garage             Pet Store   
166                Bus Station  Furniture / Home Store                   Bar   
211  Latin American Restaurant                    Park              Wine Bar   
252               Dessert Shop                     Zoo   Empanada Restaurant   
259                Bus Station     Fried Chicken Joint  Fast Food Restaurant   
279                Auto Garage                     Zoo   Empanada Restaurant   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
22             Flower Shop           Flea Market                 Field   
43           Grocery Store                   Zoo     Food & Drink Shop   
68                    Food           Flower Shop           Flea Market   
71                    Food           Flower Shop           Flea Market   
106    Empanada Restaurant           Flower Shop           Flea Market   
133  Entertainment Service                  Food           Flower Shop   
157            Flower Shop           Flea Market                 Field   
165                    Zoo   Empanada Restaurant           Flower Shop   
166                    Zoo                  Food           Flower Shop   
211                    Bar                   Zoo   Empanada Restaurant   
252                   Food           Flower Shop           Flea Market   
259      Food & Drink Shop           Flower Shop           Flea Market   
279                   Food           Flower Shop           Flea Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
22   Fast Food Restaurant        Farmers Market                Factory  
43            Flower Shop           Flea Market                  Field  
68                  Field  Fast Food Restaurant         Farmers Market  
71                  Field  Fast Food Restaurant         Farmers Market  
106                 Field  Fast Food Restaurant         Farmers Market  
133           Flea Market                 Field   Fast Food Restaurant  
157  Fast Food Restaurant        Farmers Market                Factory  
165           Flea Market                 Field   Fast Food Restaurant  
166           Flea Market                 Field   Fast Food Restaurant  
211           Flower Shop           Flea Market                  Field  
252                 Field  Fast Foo

Neighborhoods in cluster 2 seem to be surrounded by bus stations, mostly, as well as miscellaneous categories not related with the food and beverages industry. Again, not the best match for our Starbucks shop.

#### Cluster 3

In [43]:
uio_merged.loc[uio_merged['Cluster Labels'] == 2, uio_merged.columns[[2] + list(range(5, uio_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
14    COLINAS DEL SUR               2                   Gym   
44        LA ESTANCIA               2                   Gym   
143          YAGUACHI               2                   Gym   
177       LA LIBERTAD               2                   Gym   
314   SANTA LUCICIA 2               2                   Gym   
320  S.FRANC  HUARCAY               2                   Gym   
359      BUENOS AIRES               2                   Gym   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
14                    Zoo           Flower Shop           Flea Market   
44                    Zoo           Flower Shop           Flea Market   
143   Fried Chicken Joint     Food & Drink Shop           Flower Shop   
177                   Zoo           Flower Shop           Flea Market   
314             Gift Shop     Food & Drink Shop           Flower Shop   
320                   Zoo           Flower Shop           Flea Market   
359              Bus Line                   Zoo           Flower Shop   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
14                  Field  Fast Food Restaurant        Farmers Market   
44                  Field  Fast Food Restaurant        Farmers Market   
143           Flea Market                 Field  Fast Food Restaurant   
177                 Field  Fast Food Restaurant        Farmers Market   
314           Flea Market                 Field  Fast Food Restaurant   
320                 Field  Fast Food Restaurant        Farmers Market   
359           Flea Market                 Field  Fast Food Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
14                Factory           Event Space          Event Service  
44                Factory           Event Space          Event Service  
143        Farmers Market               Factory            Event Space  
177               Factory           Event Space          Event Service  
314        Farmers Market               Factory            Event Space  
320               Factory           Event Space          Event Service  
359        Farmers Market               Factory            Event Space

Neighborhoods in cluster 3 seem to be surrounded by gyms, mostly, as well as zoos flea markets and flower shops. Again, not the best match for our Starbucks shop.

#### Cluster 4

In [45]:
uio_merged.loc[uio_merged['Cluster Labels'] == 3, uio_merged.columns[[2] + list(range(5, uio_merged.shape[1]))]]

Neighborhood  Cluster Labels       1st Most Common Venue  \
11   PRESIDENCIA REPUBLICA               3          Seafood Restaurant   
35                MADRIGAL               3                  Restaurant   
36          S.PEDRO MONJAS               3        Fast Food Restaurant   
41         MIRAFLORES BAJO               3                Burger Joint   
50           LOS ARRAYANES               3                 Pizza Place   
61          VERTIENTES SUR               3          Seafood Restaurant   
73        PABLO ART SUAREZ               3  Construction & Landscaping   
80             CHIMBACALLE               3                  Print Shop   
83            MONGE DONOSO               3                 Bus Station   
98             LA VICTORIA               3          Seafood Restaurant   
108                    S/N               3              Breakfast Spot   
110            BARRIONUEVO               3                 Pizza Place   
169             LA CHILENA               3                  Restaurant   
174        JULIO MATOVELLE               3          Seafood Restaurant   
180       RECREO CLEMENCIA               3          Seafood Restaurant   
189               EL TEJAR               3                  Restaurant   
195             AGUA CLARA               3        Fast Food Restaurant   
197             LA KENNEDY               3          Seafood Restaurant   
201         6 DE DICIEMBRE               3          Seafood Restaurant   
205            LA VICTORIA               3          Seafood Restaurant   
217       FERROVIARIA BAJA               3                Soccer Field   
222       DELIC 1 PLAZA GY               3               Grocery Store   
233            ALMA LOJANA               3        Fast Food Restaurant   
241         1RA ZONA AEREA               3                 Bus Station   
248      EJERCITO NACIONAL               3                        Food   
250        1RO MAYO MONJAS               3                        Park   
254       UNION Y PROGRESO               3          Seafood Restaurant   
274             RUMINIAHUI               3          Seafood Restaurant   
297        NUEVA AURORA II               3                Noodle House   
302           MONJAS MEDIO               3              Breakfast Spot   
305            LA VICTORIA               3          Seafood Restaurant   
316       CALIFORN BONANZA               3              Ice Cream Shop   
327               JIPIJAPA               3          Seafood Restaurant   
329           2 DE FEBRERO               3            Business Service   
339             SANTA RITA               3            Asian Restaurant   
344               NAZARETH               3          Seafood Restaurant   
347         LA ECUATORIANA               3               Big Box Store   
349          S.ISIDRO INCA               3          Seafood Restaurant   
350       EJERCIT NAC 2ETP               3                        Food   

          2nd Most Common Venue 3rd Most Common Venue  \
11         Fast Food Restaurant           Pizza Place   
35   Construction & Landscaping    Seafood Restaurant   
36                   Restaurant        Clothing Store   
41         Fast Food Restaurant           Snack Place   
50                 Burger Joint          Soccer Field   
61                    BBQ Joint                   Zoo   
73      Health & Beauty Service    Seafood Restaurant   
80                        Diner    Chinese Restaurant   
83                        Motel        Clothing Store   
98          Fried Chicken Joint                 Hotel   
108            Business Service    Seafood Restaurant   
110          Seafood Restaurant   Sporting Goods Shop   
169          Seafood Restaurant                   Zoo   
174                 Pizza Place    Chinese Restaurant   
180                         Zoo            Donut Shop   
189          Seafood Restaurant         Shopping Mall   
195                 Pizza Place    Seafood Restaurant   
197                  Food T

This is the first cluster in which its neighborhoods seem to have a high variety of restaurants, which are related to a coffee shop. This cluster is a good candidate for Starbucks to consider when opening their first coffee shop in Quito.

#### Cluster 5

In [46]:
uio_merged.loc[uio_merged['Cluster Labels'] == 4, uio_merged.columns[[2] + list(range(5, uio_merged.shape[1]))]]

Neighborhood  Cluster Labels          1st Most Common Venue  \
0              NUEVA VIDA               4              Convention Center   
1              VENCEREMOS               4              Convention Center   
2          AVIACION CIVIL               4                     Restaurant   
3       S.MARTHA ALT CHIL               4                       Bus Stop   
4               LA RAYA A               4                     Restaurant   
5         RUPERTO ALARCON               4              Electronics Store   
6                 SOLANDA               4              Convenience Store   
7          EUGENIO ESPEJO               4                 Breakfast Spot   
8              SANTIAGO 1               4                    Supermarket   
9        S.ROSA CHIL 3ETP               4              Convention Center   
10       UNIVERSI CENTRAL               4                      Nightclub   
12         FRANKLIN TELLO               4                           Park   
13             S.FERNANDO               4           Gym / Fitness Center   
15       FELIXRIVADENEIRA               4                         Bakery   
16               DAMMER 2               4             Seafood Restaurant   
18              LA MERCED               4                     Restaurant   
19       STA.ROSA SINGUNA               4              Electronics Store   
20           LOS CIPRESES               4                    Coffee Shop   
21           SANTA INES 2               4                      BBQ Joint   
23               EL GUABO               4                     Restaurant   
24            HDA GUAPULO               4                     Theme Park   
25       STA BARBARA BAJA               4                     Restaurant   
26           LOS CIPRESES               4                    Coffee Shop   
28        S.CARLOS VENCEN               4                         Bakery   
29            EL TRANSITO               4      South American Restaurant   
30       PROF MUNICIPALES               4                     Restaurant   
31                LA ISLA               4              Martial Arts Dojo   
32             AREA VERDE               4            Sporting Goods Shop   
33             LA FLORIDA               4                    Pizza Place   
34              MALDONADO               4                   Burger Joint   
37              S.AGUSTIN               4                  Women's Store   
38            BELLA MARIA               4                     Restaurant   
39          ESPERANZA BAR               4            Sporting Goods Shop   
40     JARDINES DEL BATAN               4             Seafood Restaurant   
42       COND.S.PICHINCHA               4                   Burger Joint   
45         STA.LUCIA ALTA               4                   Tennis Court   
46           GERMAN AVILA               4                           Pool   
47       JOSEFINAENRIQUEZ               4                       Pharmacy   
48              EL CARMEN               4              Convenience Store   
49          LIBERTAD BAJO               4                      Pool Hall   
51                 DAMMER               4             Seafood Restaurant   
52            EL PEDREGAL               4                         Bakery   
53             MIRAFLORES               4              Food & Drink Shop   
54            EL PORVENIR               4            Indie Movie Theater   
55         HERMANO MIGUEL               4                            Gym   
56           AEREONAUTICO               4                   Soccer Field   
57                 BILOXI               4                     Restaurant   
58           LOMA HERMOSA               4                         Museum   
59                GUAJALO               4           Fast Food Restaurant   
60           MONTE OLIVOS               4           Gym / Fitness Center   
62             SAN MARCOS               4                          Hotel   
63       LA LIBERTAD ALTO               4                    

Cluster 5 is the largest and least specific cluster we obtained. Its structure is hard to interpret, given that its most common venues don't seem to be related. It may or may not be a good fit for Starbucks ideal neighborhood. However, on closer inspection, its neighborhoods seem to be all over the place, including areas far away from the city center and closer to the mountains and the city limits. Sadly, this geographical dispersion disqualifies cluster 5. Further analysis of this cluster should be conducted in order to better understand its underlying structure. 

### This concludes the data analysis we will be performing. Please refer to the attached report for an analysis and discussion of this results, as well as the conclusion and choice of the best cluster of neighborhoods for Starbucks to open their first coffee shop in Quito, Ecuador.